# Introduction to Machine Learning with Python 


## Module 2

### Learning Activity 1: Load the required libraries


In [1]:
import scipy
import numpy as np
import pandas as pd
import plotly.plotly as py

import visplots

from plotly.graph_objs import *
from plotly.offline import download_plotlyjs, init_notebook_mode, iplot
from sklearn import preprocessing, metrics
from sklearn.cross_validation import train_test_split, cross_val_score
from sklearn.neighbors import KNeighborsClassifier
from sklearn.ensemble import RandomForestClassifier
from sklearn.tree import DecisionTreeClassifier
from sklearn.grid_search import GridSearchCV, RandomizedSearchCV
from scipy.stats.distributions import randint

init_notebook_mode()

print("libraries all imported, ready to go")

libraries all imported, ready to go


### Learning Activity 2: Importing the data

The dataset we will be using throughout this workshop is an adapted version of the Wine Quality case study, available from the UCI Machine Learning repository (https://archive.ics.uci.edu/ml/datasets/Wine+Quality). The goal of this case study is to model the wine quality (into "low" or "high" quality) based on physicochemical tests (such as fixed and volatile acidity, citric acid, etc.).


The first thing you will need to do in order to work with the wine quality dataset is to read the contents from the provided `wine_quality.csv` data file using the `read_csv` command. You should also try to explore the first few rows of the imported wine DataFrame using the `head` function from the `pandas` package (http://pandas.pydata.org/pandas-docs/stable/generated/pandas.DataFrame.head.html):

In [50]:
df = pd.read_csv('data/wine_quality.csv')
header = df.columns.values
df.head()

fixed_acidity  volatile_acidity  citric_acid  residual_sugar  chlorides  \
0            7.4              0.70         0.00             1.9      0.076   
1            7.8              0.88         0.00             2.6      0.098   
2            7.8              0.76         0.04             2.3      0.092   
3           11.2              0.28         0.56             1.9      0.075   
4            7.4              0.70         0.00             1.9      0.076   

   free_sulfur_dioxide  total_sulfur_dioxide  density    pH  sulphates quality  
0                   11                    34   0.9978  3.51       0.56     low  
1                   25                    67   0.9968  3.20       0.68     low  
2                   15                    54   0.9970  3.26       0.65     low  
3                   17                    60   0.9980  3.16       0.58     low  
4                   11                    34   0.9978  3.51       0.56     low

In order to feed the data into our classification models and sklearn, the imported wine quality DataFrame needs to be converted into a `numpy` array. For more information on numpy arrays, see http://scipy-lectures.github.io/intro/numpy/array_object.html. 

In addition, it is **always** a good practice to check the dimensionality of the imported data using the `shape` command prior to constructing any classification model to make sure you have really imported all the data, and imported it in the correct way (e.g. one common mistake is to get the separator wrong and end up with only one column). 

In [6]:
np_array = np.array(df)
np_array.shape

(1487, 11)

### Test Activity 3: Inspect your data by indexing and index slicing

To select elements in an array, you specify their indices with square bracket notation. For a two-dimensional array, the first index indicates the row number and the second index indicates the column number. Try selecting the values of the first and second columns of the first sample in the npArray:

In [12]:
print(np_array[0])
print(np_array[:,0])

[7.4 0.7 0.0 1.9 0.076 11.0 34.0 0.9978 3.51 0.56 'low']
[7.4 7.8 7.8 ..., 7.9 7.9 7.1]


In [13]:
# Print the 1st row and 2nd column of npArray
print(np_array[0])
print(np_array[:,1])

[7.4 0.7 0.0 1.9 0.076 11.0 34.0 0.9978 3.51 0.56 'low']
[0.7 0.88 0.76 ..., 0.41 0.44 0.44]


To select ranges of elements, we use "index slicing". Index slicing is the technical name for the syntax A[lower:upper], where lower refers to the lower bound index that is included, and upper refers to the upper bound index that is not included. Try selecting the first three samples (rows):

In [14]:
# Print the first 3 rows of npArray
print(np_array[:3])

[[7.4 0.7 0.0 1.9 0.076 11.0 34.0 0.9978 3.51 0.56 'low']
 [7.8 0.88 0.0 2.6 0.098 25.0 67.0 0.9968 3.2 0.68 'low']
 [7.8 0.76 0.04 2.3 0.092 15.0 54.0 0.997 3.26 0.65 'low']]


and also the first three samples (rows) of the last column:

In [29]:
# Print the first 3 rows from the last column of npArray
print(np_array[:3,-1])

['low' 'low' 'low']


### Learning Activity 4: Split the data into input features, X, and outputs, y

Subsequently, we need to split our initial dataset into the data matrix X (independent variable) and the associated class vector y (dependent or target variable). The input features, _X_,  are the variables that you use to predict the outcome. In this data set, there are ten input features stored in columns 1-10 (index 0-9, although the upper bound is not included so the range for indexing is 0:10), all of which have continuous values. The output label, _y_, holds the information of whether the wine has been rated as high or low quality, and is stored in the final (eleventh) column (index 10). To split the data, we need to assign the columns of the input features and the columns of the output labels to different arrays:

In [39]:
# Split to input matrix X and class vector y
X = np_array[:,:10].astype(float)
X.shape
X[:10]
y = np_array[:, -1]
print X[:3]

[[  7.40000000e+00   7.00000000e-01   0.00000000e+00   1.90000000e+00
    7.60000000e-02   1.10000000e+01   3.40000000e+01   9.97800000e-01
    3.51000000e+00   5.60000000e-01]
 [  7.80000000e+00   8.80000000e-01   0.00000000e+00   2.60000000e+00
    9.80000000e-02   2.50000000e+01   6.70000000e+01   9.96800000e-01
    3.20000000e+00   6.80000000e-01]
 [  7.80000000e+00   7.60000000e-01   4.00000000e-02   2.30000000e+00
    9.20000000e-02   1.50000000e+01   5.40000000e+01   9.97000000e-01
    3.26000000e+00   6.50000000e-01]]


Try printing the size of the input matrix _X_ and class vector _y_ using the "`shape`" command:

In [32]:
# Print the dimensions of X and y
print(y.shape)
print(X.shape)
print y

(1487,)
(1487, 10)
['low' 'low' 'low' ..., 'high' 'high' 'high']


## Exploratory Data Analysis

Visualisation is an integral part of Data Science. Exploratory data analysis (EDA) is the field dealing with the analysis of data sets as a means of summarising their main characteristics, most often using visual methods.

Plotly is an online collaborative data analysis and graphing tool that we will use in order to construct fully interactive graphs. The Plotly API allows you to access all of the library's interactive functionality directly from Python (or other programming languages such as R, JavaScript and MATLAB, among others). Crucially, Plotly has recently been made **open-source**, which now enables plotting **offline** without requiring access to their API. _Plotly Offline_ brings interactive Plotly graphs to the _offline_ Jupyter (IPython) Notebook environment.


### Learning Activity 5:  Investigate the y frequencies

An important aspect to understand before applying any classification algorithms is how the output labels are distributed. Are they evenly distributed? Imbalances in distribution of labels can often lead to poor classification results for the minority class even if the classification results for the majority class are very good. 

In [38]:
# Print the y frequencies
yFreq = scipy.stats.itemfreq(y)
print(yFreq)

[['high' 500]
 ['low' 987]]


In our current dataset, you can see that the _y_ values are categorical (i.e. they can only take one of a discrete set of values) and have a non-numeric representation, "high" vs. "low". This can be problematic for scikit-learn and plotting functions in Python, since they assume numerical values, so we need to map the text categories to numerical representations using `LabelEncoder`  and the `fit_transform` function from the `preprocessing` module:

In [40]:
# Convert the categorical to numeric values, and print the y frequencies
le = preprocessing.LabelEncoder()
y  = le.fit_transform(y)
yFreq = scipy.stats.itemfreq(y)
print(yFreq)

[[  0 500]
 [  1 987]]


Visualising the data in some way is a good way to get a feel for how the data is distributed. As a simple example, try plotting the frequencies of the class labels (held in _yFreq_), 1 and 0, and see how they are distributed using a barplot from Plotly:

In [41]:
# Display the y frequencies in a barplot with Plotly
# (1) Create the Data object
data = [
    Bar(
        x = ['High Quality', 'Low Quality'],
        y = [yFreq[0][1], yFreq[1][1]],
        marker = dict(color=['blue','red'])
    )
]

# (2) Create a Layout object
layout = Layout(
    xaxis = dict(title = "Wine Quality"),
    yaxis = dict(title = "Count"),
    width = 500
)

# (3) Create a Figure object
fig = dict(data = data, layout = layout)

# (4) Plot
iplot(fig)


More examples on Plotly barplots can be found at https://plot.ly/python/bar-charts/. In addition, a full list of arguments on barplots can be found at https://plot.ly/python/reference/#bar/.


### Learning Activity 6: Data scaling

It is usually advisable to scale your data prior to fitting a classification model to avoid attributes with
greater numeric ranges dominating those with smaller numeric ranges. In order to investigate the range and descriptive statistics of our features, we can apply the `describe()` function from `pandas` to the original `wineQ` DataFrame (**_not_** the numpy array!). For instance:

In [42]:
# Print the descriptive statistics of the wineQ DataFrame
df.describe()

fixed_acidity  volatile_acidity  citric_acid  residual_sugar  \
count    1487.000000       1487.000000  1487.000000     1487.000000   
mean        8.272966          0.465716     0.303423        2.898588   
std         1.784884          0.192836     0.180989        2.198372   
min         4.600000          0.080000     0.000000        0.900000   
25%         7.000000          0.317500     0.170000        1.900000   
50%         7.900000          0.440000     0.320000        2.200000   
75%         9.200000          0.600000     0.430000        2.800000   
max        15.900000          1.330000     1.000000       15.500000   

         chlorides  free_sulfur_dioxide  total_sulfur_dioxide      density  \
count  1487.000000          1487.000000           1487.000000  1487.000000   
mean      0.079183            18.746469             61.755884     0.996225   
std       0.047974            12.936183             45.799977     0.002646   
min       0.012000             1.000000              6.000000     0.989000   
25%       0.059000             9.000000             25.000000     0.994965   
50%       0.076000            15.000000             47.000000     0.996720   
75%       0.088000            27.000000             93.000000     0.997905   
max       0.611000            82.000000            289.000000     1.003200   

                pH    sulphates  
count  1487.000000  1487.000000  
mean      3.293692     0.639388  
std       0.154856     0.180488  
min       2.740000     0.250000  
25%       3.190000     0.530000  
50%       3.300000     0.610000  
75%       3.390000     0.720000  
max       3.900000     2.000000

Boxplots are a powerful visual aid, commonly used in order to investigate simultaneously the range differences of the input features. Boxplots are a standardised way of displaying the distribution of the data based on the "five number summary" (minimum, first quartile, median, third quartile, and maximum). For example, try and plot the features of the _raw_ matrix _X_ using the script for the boxplots:

In [51]:
# Create a boxplot of the raw data
nrow, ncol = X.shape
data = [
    Box(
        y = X[:,i],        # values to be used for box plot
        name = header[i],  # label (on hover and x-axis)
        marker = dict(color = "purple"),
    ) for i in range(ncol)
]

layout = Layout(
    xaxis = dict(title = "Feature"),
    yaxis = dict(title = "Value"),
    showlegend=False
)

fig = dict(data = data, layout = layout)

iplot(fig)


There are many ways of scaling but one common scaling mechanism is auto-scaling, where for each
column, the values are centred around the mean and divided by their standard deviation. This scaling
mechanism can be applied by calling the `scale()` function in scikit-learn’s `preprocessing` module.

In [53]:
# Auto-scale the data
X = preprocessing.scale(X)

Try to re-run the previous plotting script and have a look at the outcome of the boxplot after scaling. Alternatively, 
if you feel more adventurous, you create a more enhanced version of the boxplot. You can find more online examples at https://plot.ly/python/box-plots/, and also a full list of boxplot arguments at https://plot.ly/python/reference/#box.


In [54]:
# Create a boxplot of the scaled data (simple or enhanced)
data = [
    Box(
        y = X[:,i],        # values to be used for box plot
        name = header[i],  # label (on hover and x-axis)
        #marker = dict(color = "purple"),
    ) for i in range(ncol)
]

layout = Layout(
    xaxis = dict(title = "Feature"),
    yaxis = dict(title = "Value"),
    showlegend=False
)

fig = dict(data = data, layout = layout)

iplot(fig)


### Learning Activity 7: Investigate the relationship between input features

You can visualise the relationship between two variables (features) using a simple scatter plot. This step can give you a good first indication of the ML model model to apply and its complexity (linear vs. non-linear). At this stage, let’s plot the first two variables against each other:

In [57]:
# Create a scatter plot of the first two features
data = [
    Scatter(
        x = X[:, 0],
        y = X[:, 1],
        mode = "markers"
    )
]

layout = Layout(
    xaxis = dict(title = header[0]),
    yaxis = dict(title = header[1])
)

fig = dict(data = data, layout = layout)

iplot(fig)

We can also relate associations between features to their y classifications by making the colour of
the points dependent on the corresponding _y_ value:

In [58]:
# Create an enhanced scatter plot of the first two features
f1 = 0
f2 = 1

# Low quality (class "1") represented with red x
trace1 = Scatter(
    x = X[y == 1, f1],
    y = X[y == 1, f2],
    mode = 'markers',
    name = 'Low Quality ("1")',
    marker = dict(
        color  = 'red',
        symbol = 'x'
    )
)

# High quality (class "0") represented with blue circles
trace2 = Scatter(
    x = X[y == 0, f1],
    y = X[y == 0, f2],
    mode = 'markers',
    name = 'High Quality ("0")',
    marker = dict(
        color  = 'blue',
        symbol = 'circle'
    )
)

layout = Layout(
    xaxis = dict(title = header[f1]),
    yaxis = dict(title = header[f2]),
    height= 600
)

fig = dict(data = [trace1, trace2], layout = layout)

iplot(fig)


Examples of Plotly scatterplots can be found at https://plot.ly/python/line-and-scatter/ (or for a list of arguments refer to https://plot.ly/python/reference/#scatter/).


### Bonus Activity 8:  Try plotting different combinations of three features (f1, f2, f3) in the same plot.


The scatterplots we have seen so far investigated the relationship between two variables (features). A three-dimensional graph lets you introduce a third axis, typically called the _z_ axis, and can help you understand the relationship between three variables. Plotly's fully interactive functionality allows you to plot, hover, zoom and rotate 3-dimensional scatterplots. For a full list of arguments on 3d plots in Plotly visit https://plot.ly/python/reference/#scatter3d. Other examples on 3D scatterplots using Plotly can be found at https://plot.ly/python/3d-scatter-plots/.

_Hint: Investigate the Scatter3d object from Plotly_

_Axes in 3D Plotly plots work a bit differently than in 2D (axes are bound to a Scene object -- use help(Scene))._


In [ ]:
# Create a 3D scatterplot using the first three features

### Bonus Activity 9: Try different combinations of f1 and f2 (in a grid/scatterplot matrix if you can).


A scatterplot matrix shows a grid of scatterplots where each attribute is plotted against all other attributes. For example, try to create a scatterplot matrix of the first four features.
You can find further information on how to create and customise subplots with Plotly at https://plot.ly/python/subplots/.

_Hints: You may want to use nested loops that iterate through the rows and columns of the grid, and also import and make use of the_ `make_subplots()` _function from Plotly_

In [ ]:
# Create a grid plot of scatterplots using a combination of features

### Bonus Activity 10: Create a correlation matrix and plot a heatmap of correlations between the input features in X

Often, the different features (variables) in X are not completely independent from each other. For example,
fixed acidity is related to volatile acidity. To quickly identify which features are related and to
what extent, it is useful to see how they are correlated. You can do this by creating a correlation matrix
from X using `corrcoef()` in the `numpy` module:

In [ ]:
# Calculate the correlation coefficient

To search for linear relationships between features across all pairs of features, you can use a heatmap
of correlations (directly from X), which is simply a matrix of subplots whose colours represent the
sizes of the correlations:

In [ ]:
# Create a heatmap of the correlation coefficients

## Module 3

### Learning Activity 1: Split the data into training and test sets

Training and testing a classification model on the same dataset is a methodological mistake: a model that would just repeat the labels of the samples that it has just seen would have a perfect score but would fail to predict anything useful on yet-unseen data (poor generalisation). To use different datasets for training and testing, we need to split the wine dataset into two disjoint sets: train and test (**Holdout method**) using the `train_test_split` function. <br/> 

In [59]:
# Split into training and test sets
XTrain, XTest, yTrain, yTest = train_test_split(X, y, random_state=1)

XTrain and yTrain are the two arrays you use to train your model. XTest and yTest are the two arrays that you use to evaluate your model. By default, scikit-learn splits the data so that 25% of it is used for testing, but you can also specify the proportion of data you want to use for training and testing.

<br/>You can check the sizes of the different training and test sets by using the `shape` attribute:

In [61]:
# Print the dimensionality of the individual splits
print(len(XTrain))
print(len(XTest))

1115
372


You can also investigate how the class labels are distributed within the *yTest* vector by using the `itemfreq` function as previously

In [62]:
# Calculate the frequency of classes in yTest
scipy.stats.itemfreq(yTest)

array([[  0, 129],
       [  1, 243]])

We can see that 129 random samples of class 0 (high quality) and 243 random samples of class 1 (low quality) are included in the yTest set.


### Learning Activity 2: Apply KNN classification algorithm with scikit-learn

To build KNN models using scikit-learn, you will be using the `KNeighborsClassifier` object, which allows you to set the value of K using the `n_neighbors` parameter (http://scikit-learn.org/stable/modules/generated/sklearn.neighbors.KNeighborsClassifier.html). The optimal choice for the value K is highly data-dependent: in general a larger K suppresses the effects of noise, but makes the classification boundaries less distinct. <br/>


For every classification model built with scikit-learn, we will follow four main steps: 1) **Building** the classification model (using either default, pre-defined or optimised parameters), 2) **Training** the model with data, 3) **Testing** the model, and 4) **Performance evaluation** using various metrics. <br/> <br/>

We are going to start by trying two pre-defined random values of K and compare their performance. Let us start with a small number of K such as K=3.

In [73]:
# Build a KNN classifier with 3 nearest neighbors
kNN3 = KNeighborsClassifier(n_neighbors=3)
kNN3.fit(XTrain, yTrain)
ypred3 = kNN3.predict(XTest)
print("Overall Accuracy:", round(metrics.accuracy_score(yTest, ypred3), 3))

('Overall Accuracy:', 0.866)


Let us try a larger value of K, for instance K = 99 or another number of your own choice; remember, it is good practice to select an **odd** number for K in a binary classification problem to avoid ties. Can you generate the KNN model and print the overall performance for a larger K (such as K=99) using as guidance the previous example? 

In [78]:
# Build a KNN classifier with 99 nearest neighbors
kNN99 = KNeighborsClassifier(n_neighbors=5)
kNN99.fit(XTrain, yTrain)
ypred99 = kNN99.predict(XTest)
print("Overall Accuracy:", round(metrics.accuracy_score(yTest, ypred99), 3))

('Overall Accuracy:', 0.887)


### Learning Activity 3: Calculate validation metrics for your classifier

In a classification task, once you have created your predictive model, you will need to evaluate it. Evaluation functions help you to do this by reporting the performance of the model through four main performance metrics: precision, recall and specificity for the different classes, and overall accuracy. To understand these metrics, it is useful to create a _confusion matrix_, which records all the true positive, true negative, false positive and false negative values.

We can compute the confusion matrix for our classifier using the `confusion_matrix` function in the `metrics` module.


In [86]:
# Get the confusion matrix for your classifier using metrics.confusion_matri
metrics.confusion_matrix(yTest, ypred3)

array([[ 99,  30],
       [ 20, 223]])


Because performance metrics are such an important step of model evaluation, scikit-learn offers a wrapper around these functions, `metrics.classification_report`, to facilitate their computation. It also offers the function `metrics.accuracy_score` that we tried before to compute the overall accuracy.


In [87]:
# Report the metrics using metrics.classification_report
print(metrics.classification_report(yTest, ypred3))

             precision    recall  f1-score   support

          0       0.83      0.77      0.80       129
          1       0.88      0.92      0.90       243

avg / total       0.86      0.87      0.86       372



### Learning Activity 4: Plot the decision boundaries for different models

We can visualise the classification boundary created by the KNN classifier using the built-in function `visplots.knnDecisionPlot`. For easier visualisation, you can (interactively) select to view only the test samples from the plot. Remember though that the decision boundary has been built using the _training_ data! <br/> 

In [89]:
# Check the arguments of the function
help(visplots.knnDecisionPlot)

# Visualise the boundaries
visplots.knnDecisionPlot(XTrain, yTrain, XTest, yTest, header, n_neighbors = 3)
visplots.knnDecisionPlot(XTrain, yTrain, XTest, yTest, header, n_neighbors = 99)

Help on function knnDecisionPlot in module visplots:

knnDecisionPlot(XTrain, yTrain, XTest, yTest, header, n_neighbors, weights='uniform')



** For smaller values of K the decision boundaries present many "creases". In this case the models may suffer from instances of overfitting. For larger values of K, we can see that the decision boundaries are less distinct and tend towards linearity. In these cases the boundaries may be too simple and unable to learn thus leading to cases of underfitting. **

### Test Activity 5: Try different weight configurations

Under some circumstances, it is better to give more importance ("weight" in computing terms) to nearer neighbors. This can be accomplished through the `weights` parameter.  When `weights = 'distance'`, weights are assigned to the training data points in a way that is proportional to the inverse of the distance from the query point. In other words, nearer neighbors contribute more to the fit. <br/>

What if we use weights based on distance? Does it improve the overall performance?

In [97]:
# Build the classifier with two pre-defined parameters (n_neighbors and weights)
kNN3 = KNeighborsClassifier(n_neighbors=5, weights='distance')
kNN3.fit(XTrain, yTrain)
ypred3 = kNN3.predict(XTest)

print(metrics.accuracy_score(yTest, ypred3))
print(metrics.confusion_matrix(yTest, ypred3))

# Visualise the boundaries of a KNN model with weights equal to "distance"
visplots.knnDecisionPlot(XTrain, yTrain, XTest, yTest, header, n_neighbors = 5, weights='distance')

0.900537634409
[[103  26]
 [ 11 232]]


## Module 4

### Learning Activity 1: Implement k-fold cross-validation

Let us estimate the accuracy of the classifier on the wine quality dataset by splitting the data 5 consecutive times (the parameter cv gives the number of samples the data is split into) using the cross_val_score function. For example, try to implement cross-validation for knn3, your KNN model with k=3:

In [104]:
# Implement cross-validation for knn3
knn3scores = cross_val_score(kNN3, X, y, cv = 3)
print(knn3scores)
print("Mean of scores KNN3", knn3scores.mean())

[ 0.69354839  0.84677419  0.81010101]
('Mean of scores KNN3', 0.78347453024872393)


What happens if we change the number of _K_?

### Parameter Tuning

### Learning Activity 2: Grid search on hyperparameters

Rather than trying one-by-one predefined values of K, we can automate this process. The scikit-learn library provides the grid search function `GridSearchCV` (http://scikit-learn.org/stable/modules/generated/sklearn.grid_search.GridSearchCV.html), which allows us to exhaustively search for the optimum combination of parameters by evaluating models trained with a particular algorithm with all provided parameter combinations. Further details and examples on grid search with scikit-learn can be found at http://scikit-learn.org/stable/modules/grid_search.html <br/>

You can use the `GridSearchCV` function with the validation technique of your choice (in this example, 10-fold cross-validation has been applied) to search for a parametisation of the KNN algorithm that gives a more optimal model:

In [119]:
# Grid search with 10-fold cross-validation using a dictionary of parameters
weights = ('uniform', 'distance')
n_neighbors = np.arange(1, 51, 2)
parameters = {'weights': weights, 'n_neighbors': n_neighbors}
knn = KNeighborsClassifier()
gridCV = GridSearchCV(knn, parameters, cv=10)
gridCV.fit(XTrain, yTrain)
bestNeighbors = gridCV.best_params_['n_neighbors']
bestWeight    = gridCV.best_params_['weights']

print("Best parameters: n_neighbors=", bestNeighbors, "and weight=", bestWeight)

('Best parameters: n_neighbors=', 27, 'and weight=', 'distance')


We can also graphically represent the results of the grid search using a heatmap:

In [121]:
# Visualise the grid search results using a heatmap
scores = np.zeros((len(n_neighbors), len(weights)))

# grid_scores_ contains parameter settings and scores
for score in gridCV.grid_scores_:
    ne = score[0]['n_neighbors']
    i = np.argmax(n_neighbors == ne)
    j = 0 if (score[0]['weights'] == 'uniform') else 1
    scores[i,j] = score[1]

# Make a heatmap with the performance
data = [
    Heatmap(
        x = n_neighbors,
        y = weights,
        z = scores.T,
        colorscale='Jet',
        reversescale=True,
        colorbar = dict(
            title = "Classification Accuracy",
            len = 4,
            nticks=10
        )
    )
]

layout = Layout(
    xaxis = dict(title = "Number of K nearest neighbors", tickvals = n_neighbors),
    yaxis = dict(title = "Weights"),
    height= 250
)

fig = dict(data = data, layout = layout)

iplot(fig)

When evaluating the resulting model it is important to do it on held-out samples that were not seen during the grid search process (XTest). <Br/>
So, we are testing our independent XTest dataset using the optimised model:

In [122]:
# Build the classifier using the optimal parameters detected by grid search 
knn_best = KNeighborsClassifier(n_neighbors=27, weights='distance')
knn_best.fit(XTrain, yTrain)
ypred = knn_best.predict(XTest)

print(metrics.accuracy_score(yTest, ypred))

0.89247311828


### Learning Activity 3: Systematic variation of the K neighbors, and the bias-variance trade-off

We can graphically represent and investigate how the systematic increase of the number of _K_ neighbors influences the validation, train and test accuracy (and attempt to detect cases of over- or under-fitting). 

In [123]:
# Explore the benefit of cross-validated results vs. simple training and test data separation
train_scores = []
test_scores  = []
cv_scores    = [x[0] for x in scores]

for n in n_neighbors:
    knn = KNeighborsClassifier(n_neighbors=n)
    knn.fit(XTrain, yTrain)
    train_scores.append(metrics.accuracy_score(yTrain, knn.predict(XTrain)))
    test_scores.append(metrics.accuracy_score(yTest, knn.predict(XTest)))

In [124]:
# Plot the train, test and validation accuracies
trace0 = Scatter(
    x = n_neighbors,
    y = train_scores,
    mode = "lines+markers",
    name = "Training Scores"
)

trace1 = Scatter(
    x = n_neighbors,
    y = test_scores,
    mode = "lines+markers",
    name = "Test Scores"
)

trace2 = Scatter(
    x = n_neighbors,
    y = cv_scores,
    mode = "lines+markers",
    name = "CV Scores"
)

layout = Layout(
    xaxis = dict(title = 'number of neighbors'),
    yaxis = dict(title = 'prediction accuracy')
)

fig = Figure(data=[trace0, trace1, trace2], layout=layout)

iplot(fig)

### Test Activity 4: Randomized search on hyperparameters

Unlike `GridSearchCV`, `RandomizedSearchCV` does not exhaustively try all the parameter settings. Instead, it samples a fixed number of parameter settings based on the distributions you specify (e.g. you might specify that one parameter should be sampled uniformly while another is sampled following a Gaussian distribution). The number of parameter settings that are tried is given by `n_iter`. If all parameters are presented as a list, sampling without replacement is performed. If at least one parameter is given as a distribution, sampling with replacement is used. You should use continuous distributions for continuous parameters. Further details can be found at http://scikit-learn.org/stable/modules/grid_search.html

In [127]:
# Conduct a randomised search on hyperparameters
parameters = {'n_neighbors': randint(1,200)}

randomCV = RandomizedSearchCV(KNeighborsClassifier(),
                              param_distributions=parameters, n_iter=20)

randomCV.fit(XTrain, yTrain)

RandomizedSearchCV(cv=None, error_score='raise',
          estimator=KNeighborsClassifier(algorithm='auto', leaf_size=30, metric='minkowski',
           metric_params=None, n_jobs=1, n_neighbors=5, p=2,
           weights='uniform'),
          fit_params={}, iid=True, n_iter=20, n_jobs=1,
          param_distributions={'n_neighbors': <scipy.stats._distn_infrastructure.rv_frozen object at 0x1171177d0>},
          pre_dispatch='2*n_jobs', random_state=None, refit=True,
          scoring=None, verbose=0)

In [129]:
# Print the optimal n_neighbors detected by randomised search
bestNeighbors = randomCV.best_params_['n_neighbors']
print bestNeighbors

19


We can also graphically represent the results of the randomised search using a scatterplot:

In [ ]:
# Visualise the randomised search results using a scatterplot

In [ ]:
# Build the classifier using the optimal parameters detected by randomised search

## Module 5

### Learning Activity 1:  Decision Tree

Decision Tree classifiers construct classification models in the form of a tree structure. A decision tree progressively splits the training set into smaller subsets. Each node of the tree represents a subset of the data. Once a new sample is presented to the data, it is classified according to the test condition generated for each node of the tree.

Let us build a simple decision tree with 3 layers. We will first evaluate the accuracy, then plot the decision boundaries just as we did for knn. (See http://scikit-learn.org/stable/modules/generated/sklearn.tree.DecisionTreeClassifier.html for the documentation of the classifier.)

In [132]:
# Build a Decision Tree classifier with 3 layers
dtc = DecisionTreeClassifier(max_depth=3)
dtc.fit(XTrain, yTrain)
predDT = dtc.predict(XTest)

print(metrics.classification_report(yTest, predDT))
print("Overall Accuracy:", round(metrics.accuracy_score(yTest, predDT),2))

visplots.dtDecisionPlot(XTrain, yTrain, XTest, yTest, header, max_depth=3)

             precision    recall  f1-score   support

          0       0.94      0.60      0.73       129
          1       0.82      0.98      0.89       243

avg / total       0.86      0.85      0.84       372

('Overall Accuracy:', 0.85)


### Learning Activity 2:  Random Forests

The random forests model is an `ensemble method` since it aggregates a group of decision trees into an ensemble (http://scikit-learn.org/stable/modules/ensemble.html). Ensemble learning involves the combination of several models to solve a single prediction problem. It works by generating multiple classifiers/models which learn and make predictions independently. Those predictions are then combined into a single (mega) prediction that should be as good or better than the prediction made by any one classifer. Unlike single decision trees which are likely to suffer from high Variance or high Bias (depending on how they are tuned) Random Forests use averaging to find a natural balance between the two extremes. <br/> 

Let us start by building a simple Random Forest model which consists of 100 independently trained decision trees. For further details and examples on how to construct a Random Forest, see http://scikit-learn.org/stable/modules/generated/sklearn.ensemble.RandomForestClassifier.html

In [137]:
# Build a Random Forest classifier with 100 decision trees
rfc = RandomForestClassifier(n_estimators=100, random_state=0)
rfc.fit(XTrain, yTrain)
ypred = rfc.predict(XTest)

print(metrics.accuracy_score(yTest, ypred))
print(metrics.classification_report(yTest, ypred))
print("Overall Accuracy:", round(metrics.accuracy_score(yTest, ypred),2))

0.895161290323
             precision    recall  f1-score   support

          0       0.92      0.77      0.84       129
          1       0.89      0.96      0.92       243

avg / total       0.90      0.90      0.89       372

('Overall Accuracy:', 0.9)


### Learning Activity 3: Visualising the RF accuracy

We can also investigate how the overall test accuracy gets influenced with the increase of `n_estimators` (decision trees) in our model. In order to do so, we can use the provided `rfAvgAcc` function from `visplots`:

In [139]:
# Visualise the average accuracy 
visplots.rfAvgAcc(rfModel=rfc, XTest=XTest, yTest=yTest)

### Learning Activity 4: Feature Importance 

Random forests allow you to compute a heuristic for determining how “important” a feature is in predicting a target. This heuristic measures the change in prediction accuracy if you take a given feature and permute (scramble) it across the datapoints in the training set. The more the accuracy drops when the feature is permuted, the more “important” we can conclude the feature is.

We can use the `feature_importances_` attribute of the RF classifier to obtain the relative importance of each feature, which we can then visualise using a simple bar plot.

In [140]:
# Display the importance of the features in a barplot
importance = rfc.feature_importances_
names = header[:10]

data = [
    Bar(
        x = importance,
        y = names, 
        orientation = 'h'
    )
]

layout = Layout(
    xaxis = dict(title = 'Importance of features'),
    yaxis = dict(title = 'Features'),
    width = 800,
    margin = Margin(
        l = 250,
        r = 50,
        b = 100,
        t = 50,
        pad = 4
    ),
)

fig = dict(data = data, layout = layout)

iplot(fig)

###  Learning activity 5: Boundary visualisation

We can visualise the classification boundary created by the Random Forest using the `visplots.rfDecisionPlot` function. You can check the arguments passed in this function by using the `help` command. For easier visualisation, only the test samples have been included in the plot. And remember that the decision boundary has been built using the _training_ data!

In [141]:
# Check the arguments of the function

# Visualise the boundaries
visplots.rfDecisionPlot(XTrain, yTrain, XTest, yTest, header)

### Learning Activity 6: Tuning Random Forests with grid search

Random forests offer several parameters that can be tuned. In this case, parameters such as `n_estimators`, `max_features`, `max_depth` and `min_samples_leaf` can be some of the parameters to be optimised. 

In [142]:
# View the list of arguments to be optimised
help(RandomForestClassifier())

Help on RandomForestClassifier in module sklearn.ensemble.forest object:

class RandomForestClassifier(ForestClassifier)
 |  A random forest classifier.
 |  
 |  A random forest is a meta estimator that fits a number of decision tree
 |  classifiers on various sub-samples of the dataset and use averaging to
 |  improve the predictive accuracy and control over-fitting.
 |  The sub-sample size is always the same as the original
 |  input sample size but the samples are drawn with replacement if
 |  `bootstrap=True` (default).
 |  
 |  Read more in the :ref:`User Guide <forest>`.
 |  
 |  Parameters
 |  ----------
 |  n_estimators : integer, optional (default=10)
 |      The number of trees in the forest.
 |  
 |  criterion : string, optional (default="gini")
 |      The function to measure the quality of a split. Supported criteria are
 |      "gini" for the Gini impurity and "entropy" for the information gain.
 |      Note: this parameter is tree-specific.
 |  
 |  max_features : int, f

Create a dictionary of allowed parameter ranges for `n_estimators` and `max_depth` (or include more of the parameters you would like to tune) and conduct a grid search with cross validation using the `GridSearchCV` function as before:

In [144]:
# Conduct a grid search with 10-fold cross-validation using the dictionary of parameters
n_estimators = np.arange(1, 50, 5)
max_depth    = np.arange(1, 100, 5)
parameters   = [{'n_estimators': n_estimators, 'max_depth': max_depth}]

gridCV = GridSearchCV(RandomForestClassifier(), param_grid=parameters, cv=10)
gridCV.fit(XTrain, yTrain)

# Print the optimal parameters
best_n_estim   = gridCV.best_params_['n_estimators']
best_max_depth = gridCV.best_params_['max_depth']

print ("Best parameters: n_estimators=", best_n_estim,", max_depth=", best_max_depth)

('Best parameters: n_estimators=', 46, ', max_depth=', 66)


Finally, testing our independent XTest dataset using the optimised model: 

In [ ]:
# Build the classifier using the optimal parameters detected by grid search

We can also graphically represent the results of the grid search using a heatmap:

In [ ]:
# Create a heatmap like the one you made when you applied GridSearchCV to KNN

### Bonus Activity 7: Parallelisation


The scikit-learn implementation of Random Forests also features the parallel construction of the trees and the parallel computation of the predictions through the n_jobs parameter.
If `n_jobs=k` then computations are partitioned into k jobs, and run on k cores of the machine.
If `n_jobs=-1` then all cores available on the machine are used.


In [ ]:
# Change the value of n_jobs and estimate the excution time of fit

In [ ]:
# Plot a graph